In [18]:
#######################################
# CS 424 - Project 2
# Kevin Kowalski
# Samuel Kajah
# Vijay Vemu
#######################################
#
# This file contains the code to clean
# the original data set. It outputs
# the necessary plots and updated data
# set to be used by shiny.
#
# This file was used for testing and 
# plotting before using RStudio for a
# dashboard.
#
#######################################

In [19]:
# import libraries
library(comprehenr)
library(dplyr)
library(hashmap)
library(leaflet)
library(lubridate)
library(stringr)

In [20]:
# create appropriate column names for data in the following format
"
data rows
col 1 – date YYYYmmDD
col 2 – time HHMM
col 3 – record identifier (factor)
col 4 – storm type (factor)
col 5 – latitude (n/s)
col 6 – longitude (e/w)
col 7 – Maximum sustained wind (in knots)
col 8 – Minimum Pressure (in millibars)
col 9 – 34 kt wind radii maximum extent in northeastern quadrant (in nautical miles) 
col 10 – 34 kt wind radii maximum extent in southeastern quadrant (in nautical miles) 
col 11 – 34 kt wind radii maximum extent in southwestern quadrant (in nautical miles) 
col 12 – 34 kt wind radii maximum extent in northwestern quadrant (in nautical miles) 
col 13 – 50 kt wind radii maximum extent in northeastern quadrant (in nautical miles) 
col 14 – 50 kt wind radii maximum extent in southeastern quadrant (in nautical miles) 
col 15 – 50 kt wind radii maximum extent in southwestern quadrant (in nautical miles) 
col 16 – 50 kt wind radii maximum extent in northwestern quadrant (in nautical miles) 
col 17 – 64 kt wind radii maximum extent in northeastern quadrant (in nautical miles)
col 18 – 64 kt wind radii maximum extent in southeastern quadrant (in nautical miles)
col 19 – 64 kt wind radii maximum extent in southwestern quadrant (in nautical miles) 
col 20 – 64 kt wind radii maximum extent in northwestern quadrant (in nautical miles)
"

data_row_header = c('Date', 'Time', 'Record_ID', 'Storm_Type', 'Lat', 'Lon', 'Speed', 'Pressure', 
                   'Wind_Radii_NE_34', 'Wind_Radii_SE_34', 'Wind_Radii_SW_34', 'Wind_Radii_NW_34',
                   'Wind_Radii_NE_50', 'Wind_Radii_SE_50', 'Wind_Radii_SW_50', 'Wind_Radii_NW_50',
                   'Wind_Radii_NE_64', 'Wind_Radii_SE_64', 'Wind_Radii_SW_64', 'Wind_Radii_NW_64', 'Size')

[1] "\ndata rows\ncol 1 – date YYYYmmDD\ncol 2 – time HHMM\ncol 3 – record identifier (factor)\ncol 4 – storm type (factor)\ncol 5 – latitude (n/s)\ncol 6 – longitude (e/w)\ncol 7 – Maximum sustained wind (in knots)\ncol 8 – Minimum Pressure (in millibars)\ncol 9 – 34 kt wind radii maximum extent in northeastern quadrant (in nautical miles) \ncol 10 – 34 kt wind radii maximum extent in southeastern quadrant (in nautical miles) \ncol 11 – 34 kt wind radii maximum extent in southwestern quadrant (in nautical miles) \ncol 12 – 34 kt wind radii maximum extent in northwestern quadrant (in nautical miles) \ncol 13 – 50 kt wind radii maximum extent in northeastern quadrant (in nautical miles) \ncol 14 – 50 kt wind radii maximum extent in southeastern quadrant (in nautical miles) \ncol 15 – 50 kt wind radii maximum extent in southwestern quadrant (in nautical miles) \ncol 16 – 50 kt wind radii maximum extent in northwestern quadrant (in nautical miles) \ncol 17 – 64 kt wind radii maximum extent in northeastern quadrant (in nautical miles)\ncol 18 – 64 kt wind radii maximum extent in southeastern quadrant (in nautical miles)\ncol 19 – 64 kt wind radii maximum extent in southwestern quadrant (in nautical miles) \ncol 20 – 64 kt wind radii maximum extent in northwestern quadrant (in nautical miles)\n"

In [21]:
# rename original text files to easier-to-work-with CSV files
file.rename("hurdat2-1851-2018-120319.txt", "atlantic_hurricanes.csv")
file.rename("hurdat2-nepac-1949-2018-122019.txt", "pacific_hurricanes.csv")

[1] FALSE

[1] FALSE

In [22]:
# read in the renamed CSV files
atlantic_data = read.csv('atlantic_hurricanes.csv', header = FALSE, stringsAsFactors = FALSE)
pacific_data = read.csv('pacific_hurricanes.csv', header = FALSE, stringsAsFactors = FALSE)

# apply column names to data
colnames(atlantic_data) = data_row_header
colnames(pacific_data) = data_row_header

In [23]:
# trim the first 6 string columns that contain leading/trailing whitespace
for (col in 1: 6) {
    atlantic_data[, col] = str_trim(atlantic_data[, col])
    pacific_data[, col] = str_trim(pacific_data[, col])
}

In [24]:
# create a new timestamp column containing both date and time
atlantic_data = atlantic_data %>% mutate(Timestamp = parse_date_time(paste(atlantic_data$Date, atlantic_data$Time, sep = ' '), "Ymd HM", tz = 'America/Chicago', quiet = TRUE))
pacific_data = pacific_data %>% mutate(Timestamp = parse_date_time(paste(pacific_data$Date, pacific_data$Time, sep = ' '), "Ymd HM", tz = 'America/Chicago', quiet = TRUE))

In [25]:
# the lat and long are using NESW; change it to positive/negative; because plotting only accepts numbers
# N/E = positive, S/W = negative
remake_coordinates = function(coordinates) {
    result = numeric(length(coordinates)) # empty vector of characters
    i = 1
    for(coordinate in coordinates) {
        bearing_index = nchar(coordinate)
        double_value = substr(coordinate, 1, bearing_index - 1) # get just the digits
        bearing = substr(coordinate, bearing_index, bearing_index) # get the direction
        if (bearing == "N" || bearing == "E") {
            result[i] = as.numeric(double_value)
        } else { # must be South or West
            result[i] = -as.numeric(double_value)
        }
        i = i + 1
    }
    result
}

In [26]:
# update coordinates to plot-friendly values
atlantic_data$Lat = remake_coordinates(atlantic_data$Lat)
atlantic_data$Lon = remake_coordinates(atlantic_data$Lon)
pacific_data$Lat = remake_coordinates(pacific_data$Lat)
pacific_data$Lon = remake_coordinates(pacific_data$Lon)

In [27]:
# custom functions for reading and formatting data

# determine's if a particular row begins a header for a hurricane entry (by at having at least 15 NA in its row)
is_header_row = function(row) {
    if (sum(is.na(row)) >= 15) 
        TRUE 
    else 
        FALSE
}

# create a vector of indices of all hurricane header rows
header_locations = function(data) {
    to_vec(
        for(row in 1: nrow(data)) 
            if (is_header_row(data[row, ])) 
                row)
}

# assign a new new unique name to unnamed storms
storm_name_from_header = function(header_df, prefix, id) {
    if (header_df[1, 2] == "UNNAMED") {
        paste(prefix, "STORM", id, sep = " ") # use STORM + id as new name
    } else {
        header_df[1, 2]
    }
}

# prefix is for naming unnamed storms
# if prefix is "ATLANTIC" then unnamed storms will be named 
# ATLANTIC STORM <storm_id>
make_huricane_data = function(data, header_indices, prefix) {
    tables = list() # keep track of the data associated with each storm
    i = 1 
    for(row_index in 1: length(header_indices)) {
        row = header_indices[row_index] # get the next header row index
        current_header = data[row, ] # get the header data
        storm_name = storm_name_from_header(current_header, prefix, i) # get name of the storm and add to list

    if (row_index == length(header_indices)) { # at the last header
        tables[[i]] = data[(row + 1): nrow(data), ] %>% # the data is from next row to the end of the data
            mutate(Storm_Name = storm_name) %>% # add the storm name
            mutate(Unique_ID = current_header[1, 1]) %>% # add the storm unique ID
            select(Storm_Name, Unique_ID, Timestamp, everything()) # move new columns to front for better ordering
        # adding these will make it easier to filter data
        
    } else { # otherwise, data is from next row to the start of the next header
        next_header = header_indices[row_index + 1]
        tables[[i]] = data[(row + 1): (next_header - 1), ]  %>%
            mutate(Storm_Name = storm_name) %>% # add the storm name
            mutate(Unique_ID = current_header[1, 1]) %>% # add the storm unique ID
            select(Storm_Name, Unique_ID, Timestamp, everything()) # move new columns to front for better ordering
    }
    i = i + 1
  }
  tables
}

In [28]:
# get list of all indices with hurricane headers
atlantic_header_indices = header_locations(atlantic_data)
pacific_header_indices = header_locations(pacific_data)

In [29]:
# list of dataframes of storms; this wil be the main storage for the data, makes it easy to plot
atlantic_data = make_huricane_data(atlantic_data, atlantic_header_indices, "ATLANTIC") # contains names and name_data
pacific_data = make_huricane_data(pacific_data, pacific_header_indices, "PACIFIC") # contains names and name_data

# if needed, can merge into one list 
#combined_data = c(atlantic_data, pacific_data)

In [30]:
# write the cleaned data to RDS files
saveRDS(atlantic_data, file = "atlantic_data.rds")
saveRDS(pacific_data, file = "pacific_data.rds")

In [31]:
# print head of first storm from both data sets
print("Atlantic Data")
head(atlantic_data[[1]])
print("Pacific Data")
head(pacific_data[[1]])

[1] "Atlantic Data"


Storm_Name       Unique_ID Timestamp           Date     Time Record_ID
1 ATLANTIC STORM 1 AL011851  1851-06-25 00:00:00 18510625 0000          
2 ATLANTIC STORM 1 AL011851  1851-06-25 06:00:00 18510625 0600          
3 ATLANTIC STORM 1 AL011851  1851-06-25 12:00:00 18510625 1200          
4 ATLANTIC STORM 1 AL011851  1851-06-25 18:00:00 18510625 1800          
5 ATLANTIC STORM 1 AL011851  1851-06-25 21:00:00 18510625 2100 L        
6 ATLANTIC STORM 1 AL011851  1851-06-26 00:00:00 18510626 0000          
  Storm_Type Lat  Lon   Speed ... Wind_Radii_NW_34 Wind_Radii_NE_50
1 HU         28.0 -94.8 80    ... -999             -999            
2 HU         28.0 -95.4 80    ... -999             -999            
3 HU         28.0 -96.0 80    ... -999             -999            
4 HU         28.1 -96.5 80    ... -999             -999            
5 HU         28.2 -96.8 80    ... -999             -999            
6 HU         28.2 -97.0 70    ... -999             -999            
  Wind_Radii_SE_50 Wind_Radii_SW_50 Wind_Radii_NW_50 Wind_Radii_NE_64
1 -999             -999             -999             -999            
2 -999             -999             -999             -999            
3 -999             -999             -999             -999            
4 -999             -999             -999             -999            
5 -999             -999             -999             -999            
6 -999             -999             -999             -999            
  Wind_Radii_SE_64 Wind_Radii_SW_64 Wind_Radii_NW_64 Size
1 -999             -999             -999             NA  
2 -999             -999             -999             NA  
3 -999             -999             -999             NA  
4 -999             -999             -999             NA  
5 -999             -999             -999             NA  
6 -999             -999             -999             NA

[1] "Pacific Data"


Storm_Name      Unique_ID Timestamp           Date     Time Record_ID
1 PACIFIC STORM 1 EP011949  1949-06-11 00:00:00 19490611 0000          
2 PACIFIC STORM 1 EP011949  1949-06-11 06:00:00 19490611 0600          
3 PACIFIC STORM 1 EP011949  1949-06-11 12:00:00 19490611 1200          
4 PACIFIC STORM 1 EP011949  1949-06-11 18:00:00 19490611 1800          
5 PACIFIC STORM 1 EP011949  1949-06-12 00:00:00 19490612 0000          
6 PACIFIC STORM 1 EP011949  1949-06-12 06:00:00 19490612 0600          
  Storm_Type Lat  Lon    Speed ... Wind_Radii_NW_34 Wind_Radii_NE_50
1 TS         20.2 -106.3 45    ... -999             -999            
2 TS         20.2 -106.4 45    ... -999             -999            
3 TS         20.2 -106.7 45    ... -999             -999            
4 TS         20.3 -107.7 45    ... -999             -999            
5 TS         20.4 -108.6 45    ... -999             -999            
6 TS         20.5 -109.4 45    ... -999             -999            
  Wind_Radii_SE_50 Wind_Radii_SW_50 Wind_Radii_NW_50 Wind_Radii_NE_64
1 -999             -999             -999             -999            
2 -999             -999             -999             -999            
3 -999             -999             -999             -999            
4 -999             -999             -999             -999            
5 -999             -999             -999             -999            
6 -999             -999             -999             -999            
  Wind_Radii_SE_64 Wind_Radii_SW_64 Wind_Radii_NW_64 Size
1 -999             -999             -999             NA  
2 -999             -999             -999             NA  
3 -999             -999             -999             NA  
4 -999             -999             -999             NA  
5 -999             -999             -999             NA  
6 -999             -999             -999             NA

In [32]:
# custom functions for retrieving and plotting storm data

# plot a single storm's path on a map
plot_storm_path = function(storm_data, color) { # very simple plots, but will customize later
    map_object = leaflet() %>% addTiles()
        if (nrow(storm_data) == 1) { # only 1 coordinate
            map_object %>% 
            addCircleMarkers(data = storm_data, lat = ~Lat, lng = ~Lon, color = color)
        } else {
            map_object %>% 
                addPolylines(data = storm_data, lat = ~Lat, lng = ~Lon, color = color) # %>% 
                # addMarkers(data=storm_data, lng= ~lon, lat= ~lat)
        }
}

# plot multiple storm paths on a map
plot_multi_storm_path = function(storm_data_list, color_list) {
    map_object = leaflet() %>% addTiles()
    for(i in 1: length(storm_data_list)) {
        storm_data = storm_data_list[[i]]
        color = color_list[i]
        if (nrow(storm_data) == 1) { # only 1 coordinate
            map_object = map_object %>% 
                addCircleMarkers(data = storm_data, lat = ~Lat, lng = ~Lon, color = color)
        } else {
            map_object = map_object %>% 
                addPolylines(data = storm_data, lat = ~Lat, lng = ~Lon, color = color) # %>% 
                # addMarkers(data=storm_data, lng= ~lon, lat= ~lat)
        }
    }
    map_object
}

# get a list of storms (spanning) in a given year
get_storms_by_year = function(storm_data_list, year) {
    result = list()
    i = 1 
    for (storm_data in storm_data_list) {
        # check wether the given year is in the years cuz a storm may span end of 1 year to start of another
        if (year %in% year(storm_data$Timestamp)) { 
            # get the specific year
            result[[i]] = storm_data
            i = i + 1
        }
    }
    result
}

# get a list of storms (spanning) in a given day
get_storms_by_day = function(storm_data_list, date_string) {
    # date string should be a string of the form mm/dd/YYYY (same in UI display)
    result = list()
    i = 1 
    for(storm_data in storm_data_list) {
        # check if date is in the dates (because a storm can span > 1 day)
        if (as.Date(date_string, "%m/%d/%Y") %in% as.Date(storm_data$Timestamp)) {
            result[[i]] = storm_data
            i = i + 1
        }
    }
    result 
}

# get a storm's data given its name
get_storm_by_name = function(storm_data_list, name) {
    for (storm_data in storm_data_list) {
        if (name %in% storm_data$Storm_Name) {
            return (storm_data)
        }
    }
}



In [33]:
###########################
### Example Plots Below ###
###########################

In [34]:
# plot Atlnatic storms 11 through 15 on a map
plot_multi_storm_path(atlantic_data[11:15], c("red", "blue", "gray", "pink", "purple"))

# !!! doesn't plot in notebook for some reason; needs to be run in R Studio !!!

HTML widgets cannot be represented in plain text (need html)

In [35]:
# plot Atlantic storms from 2018
colors = c("red", "blue", "gray", "pink", "purple", "black", "aqua", "royalblue",
           "yellow", "brown", "green", "turquoise", "skyblue", "fuscia", "white", "orange")
plot_multi_storm_path(get_storms_by_year(atlantic_data, 2018), colors)

HTML widgets cannot be represented in plain text (need html)

In [36]:
# get the data for the storms on June 11, 1949 and plot their paths on a map
plot_multi_storm_path(get_storms_by_day(pacific_data, "06/11/1949"), colors)

HTML widgets cannot be represented in plain text (need html)

In [37]:
# get the data for the storm named HIKI and plot its path on a map
plot_storm_path(get_storm_by_name(pacific_data, 'HIKI'), "blue")

HTML widgets cannot be represented in plain text (need html)

In [38]:
# plot a single storm's path on a map by its size
plot_storm_path_by_size = function(storm_data, color) { # very simple plots, but will customize later
    map_object = leaflet() %>% addTiles()
        if (nrow(storm_data) == 1) { # only 1 coordinate
            map_object %>% 
            addCircleMarkers(data = storm_data, lat = ~Lat, lng = ~Lon, color = color, radius = (storm_data$Speed / 20)) # add markers for size, replace radius with desired circle scaler
        } else {
            map_object %>% 
                addCircleMarkers(data = storm_data, lat = ~Lat, lng = ~Lon, color = color, radius = (storm_data$Speed / 20)) %>% # add markers for size, replace radius with desired circle scaler
                addPolylines(data = storm_data, lat = ~Lat, lng = ~Lon, color = color, weight = storm_data$Size) #%>%
                #addMarkers(data = storm_data, lng= ~Lon, lat= ~Lat)
        }
}

# plot multiple storm paths on a map by their size
plot_multi_storm_path_by_size = function(storm_data_list, color_list) {
    map_object = leaflet() %>% addTiles()
    for(i in 1: length(storm_data_list)) {
        storm_data = storm_data_list[[i]]
        color = color_list[i]
        if (nrow(storm_data) == 1) { # only 1 coordinate
            map_object = map_object %>% 
                addCircleMarkers(data = storm_data, lat = ~Lat, lng = ~Lon, color = color, radius = (storm_data$Speed / 20)) # add markers for size, replace radius with desired circle scaler
        } else {
            map_object = map_object %>% 
                addCircleMarkers(data = storm_data, lat = ~Lat, lng = ~Lon, color = color, radius = (storm_data$Speed / 20)) %>% # add markers for size, replace radius with desired circle scaler
                addPolylines(data = storm_data, lat = ~Lat, lng = ~Lon, color = color, weight = storm_data$Size) # %>% 
                # addMarkers(data=storm_data, lng= ~lon, lat= ~lat)
        }
    }
    map_object
}

# !!! all hurricanes have N/A in Size column, so using scaled down speed to plot size of hurricane at each point of its path

In [39]:
# get the data for the storm named HIKI and plot its path on a map by size
plot_storm_path_by_size(get_storm_by_name(pacific_data, 'HIKI'), "blue")

HTML widgets cannot be represented in plain text (need html)

In [40]:
# plot Atlantic storms by size from 2018
colors = c("red", "blue", "gray", "pink", "purple", "black", "aqua", "royalblue",
           "yellow", "brown", "green", "turquoise", "skyblue", "fuscia", "white", "orange")
plot_multi_storm_path_by_size(get_storms_by_year(atlantic_data, 2018), colors)

HTML widgets cannot be represented in plain text (need html)

In [41]:
################################
### Ordering Functions Below ###
################################

In [42]:
# get a table of hurricanes in chronological order for a given data set
get_storm_names_chronologically = function(storm_data_list) {
    table = list()
    i = 1
    for (storm_data in storm_data_list) {
        table[[i]] = storm_data$Storm_Name[1]
        i = i + 1
    }
    
    # build dataframe of each hurricane by name
    df <- data.frame(matrix(unlist(table), nrow = length(table), byrow = T), stringsAsFactors = FALSE)
    names(df)[1] <- "Storm_Name"
    
    # should be sorted in chronological order by default so return the ordered list of names
    df$Storm_Name
}

# get a table of hurricanes in alphabetical order for a given data set
get_storm_names_alphabetically = function(storm_data_list) {
    table = list()
    i = 1
    for (storm_data in storm_data_list) {
        table[[i]] = storm_data$Storm_Name[1]
        i = i + 1
    }
    
    # build dataframe of each hurricane by name
    df <- data.frame(matrix(unlist(table), nrow = length(table), byrow = T), stringsAsFactors = FALSE)
    names(df)[1] <- "Storm_Name"
    
    # sort in alphabetical order and return the ordered list of names
    df <- df[order(df$Storm_Name), ]
    df
}

# get a table of hurricanes in order by top speed for a given data set
get_storm_names_max_speed = function(storm_data_list) {
    table = list()
    i = 1
    for (storm_data in storm_data_list) {
        table[[i]] = c(storm_data$Storm_Name[1], max(storm_data$Speed))
        i = i + 1
    }
    
    # build dataframe of each hurricane and its top speed
    df <- data.frame(matrix(unlist(table), nrow = length(table), byrow = T), stringsAsFactors = FALSE)
    names(df)[1] <- "Storm_Name"
    names(df)[2] <- "TopSpeed"
    df$TopSpeed <- as.numeric(df$TopSpeed)
    
    # sort in descending order and return the ordered list of names
    df <- df[order(-df$TopSpeed), ]
    df$Storm_Name
}

# get a table of hurricanes in order by min pressure for a given data set
get_storm_names_min_pressure = function(storm_data_list) {
    table = list()
    i = 1
    for (storm_data in storm_data_list) {
        table[[i]] = c(storm_data$Storm_Name[1], min(storm_data$Pressure))
        i = i + 1
    }
    
    # build dataframe of each hurricane and its min pressure
    df <- data.frame(matrix(unlist(table), nrow = length(table), byrow = T), stringsAsFactors = FALSE)
    names(df)[1] <- "Storm_Name"
    names(df)[2] <- "MinPressure"
    df$MinPressure <- as.numeric(df$MinPressure)
    
    # sort in ascending order and return the ordered list of names
    df <- df[order(df$MinPressure), ]
    df$Storm_Name
}

In [43]:
# output count and chronological order of atlantic hurricanes
chrono_order <- get_storm_names_chronologically(atlantic_data)
length(chrono_order)
chrono_order

[1] 1873

[1] "ATLANTIC STORM 1"    "ATLANTIC STORM 2"    "ATLANTIC STORM 3"   
   [4] "ATLANTIC STORM 4"    "ATLANTIC STORM 5"    "ATLANTIC STORM 6"   
   [7] "ATLANTIC STORM 7"    "ATLANTIC STORM 8"    "ATLANTIC STORM 9"   
  [10] "ATLANTIC STORM 10"   "ATLANTIC STORM 11"   "ATLANTIC STORM 12"  
  [13] "ATLANTIC STORM 13"   "ATLANTIC STORM 14"   "ATLANTIC STORM 15"  
  [16] "ATLANTIC STORM 16"   "ATLANTIC STORM 17"   "ATLANTIC STORM 18"  
  [19] "ATLANTIC STORM 19"   "ATLANTIC STORM 20"   "ATLANTIC STORM 21"  
  [22] "ATLANTIC STORM 22"   "ATLANTIC STORM 23"   "ATLANTIC STORM 24"  
  [25] "ATLANTIC STORM 25"   "ATLANTIC STORM 26"   "ATLANTIC STORM 27"  
  [28] "ATLANTIC STORM 28"   "ATLANTIC STORM 29"   "ATLANTIC STORM 30"  
  [31] "ATLANTIC STORM 31"   "ATLANTIC STORM 32"   "ATLANTIC STORM 33"  
  [34] "ATLANTIC STORM 34"   "ATLANTIC STORM 35"   "ATLANTIC STORM 36"  
  [37] "ATLANTIC STORM 37"   "ATLANTIC STORM 38"   "ATLANTIC STORM 39"  
  [40] "ATLANTIC STORM 40"   "ATLANTIC STORM 41"   "ATLANTIC STORM 42"  
  [43] "ATLANTIC STORM 43"   "ATLANTIC STORM 44"   "ATLANTIC STORM 45"  
  [46] "ATLANTIC STORM 46"   "ATLANTIC STORM 47"   "ATLANTIC STORM 48"  
  [49] "ATLANTIC STORM 49"   "ATLANTIC STORM 50"   "ATLANTIC STORM 51"  
  [52] "ATLANTIC STORM 52"   "ATLANTIC STORM 53"   "ATLANTIC STORM 54"  
  [55] "ATLANTIC STORM 55"   "ATLANTIC STORM 56"   "ATLANTIC STORM 57"  
  [58] "ATLANTIC STORM 58"   "ATLANTIC STORM 59"   "ATLANTIC STORM 60"  
  [61] "ATLANTIC STORM 61"   "ATLANTIC STORM 62"   "ATLANTIC STORM 63"  
  [64] "ATLANTIC STORM 64"   "ATLANTIC STORM 65"   "ATLANTIC STORM 66"  
  [67] "ATLANTIC STORM 67"   "ATLANTIC STORM 68"   "ATLANTIC STORM 69"  
  [70] "ATLANTIC STORM 70"   "ATLANTIC STORM 71"   "ATLANTIC STORM 72"  
  [73] "ATLANTIC STORM 73"   "ATLANTIC STORM 74"   "ATLANTIC STORM 75"  
  [76] "ATLANTIC STORM 76"   "ATLANTIC STORM 77"   "ATLANTIC STORM 78"  
  [79] "ATLANTIC STORM 79"   "ATLANTIC STORM 80"   "ATLANTIC STORM 81"  
  [82] "ATLANTIC STORM 82"   "ATLANTIC STORM 83"   "ATLANTIC STORM 84"  
  [85] "ATLANTIC STORM 85"   "ATLANTIC STORM 86"   "ATLANTIC STORM 87"  
  [88] "ATLANTIC STORM 88"   "ATLANTIC STORM 89"   "ATLANTIC STORM 90"  
  [91] "ATLANTIC STORM 91"   "ATLANTIC STORM 92"   "ATLANTIC STORM 93"  
  [94] "ATLANTIC STORM 94"   "ATLANTIC STORM 95"   "ATLANTIC STORM 96"  
  [97] "ATLANTIC STORM 97"   "ATLANTIC STORM 98"   "ATLANTIC STORM 99"  
 [100] "ATLANTIC STORM 100"  "ATLANTIC STORM 101"  "ATLANTIC STORM 102" 
 [103] "ATLANTIC STORM 103"  "ATLANTIC STORM 104"  "ATLANTIC STORM 105" 
 [106] "ATLANTIC STORM 106"  "ATLANTIC STORM 107"  "ATLANTIC STORM 108" 
 [109] "ATLANTIC STORM 109"  "ATLANTIC STORM 110"  "ATLANTIC STORM 111" 
 [112] "ATLANTIC STORM 112"  "ATLANTIC STORM 113"  "ATLANTIC STORM 114" 
 [115] "ATLANTIC STORM 115"  "ATLANTIC STORM 116"  "ATLANTIC STORM 117" 
 [118] "ATLANTIC STORM 118"  "ATLANTIC STORM 119"  "ATLANTIC STORM 120" 
 [121] "ATLANTIC STORM 121"  "ATLANTIC STORM 122"  "ATLANTIC STORM 123" 
 [124] "ATLANTIC STORM 124"  "ATLANTIC STORM 125"  "ATLANTIC STORM 126" 
 [127] "ATLANTIC STORM 127"  "ATLANTIC STORM 128"  "ATLANTIC STORM 129" 
 [130] "ATLANTIC STORM 130"  "ATLANTIC STORM 131"  "ATLANTIC STORM 132" 
 [133] "ATLANTIC STORM 133"  "ATLANTIC STORM 134"  "ATLANTIC STORM 135" 
 [136] "ATLANTIC STORM 136"  "ATLANTIC STORM 137"  "ATLANTIC STORM 138" 
 [139] "ATLANTIC STORM 139"  "ATLANTIC STORM 140"  "ATLANTIC STORM 141" 
 [142] "ATLANTIC STORM 142"  "ATLANTIC STORM 143"  "ATLANTIC STORM 144" 
 [145] "ATLANTIC STORM 145"  "ATLANTIC STORM 146"  "ATLANTIC STORM 147" 
 [148] "ATLANTIC STORM 148"  "ATLANTIC STORM 149"  "ATLANTIC STORM 150" 
 [151] "ATLANTIC STORM 151"  "ATLANTIC STORM 152"  "ATLANTIC STORM 153" 
 [154] "ATLANTIC STORM 154"  "ATLANTIC STORM 155"  "ATLANTIC STORM 156" 
 [157] "ATLANTIC STORM 157"  "ATLANTIC STORM 158"  "ATLANTIC STORM 159" 
 [160] "ATLANTIC STORM 160"  "ATLANTIC STORM 161"  "ATLANTIC STORM 162" 
 [163] "ATLANTIC STORM 163"  "ATLANTIC STORM 164"  "ATLANTIC 

In [44]:
# output count and alphabetical order of atlantic hurricanes
alpha_order <- get_storm_names_alphabetically(atlantic_data)
length(alpha_order)
alpha_order

[1] 1873

[1] "ABBY"                "ABBY"                "ABBY"               
   [4] "ABLE"                "ABLE"                "ABLE"               
   [7] "AGNES"               "ALBERTO"             "ALBERTO"            
  [10] "ALBERTO"             "ALBERTO"             "ALBERTO"            
  [13] "ALBERTO"             "ALBERTO"             "ALEX"               
  [16] "ALEX"                "ALEX"                "ALEX"               
  [19] "ALFA"                "ALICE"               "ALICE"              
  [22] "ALICE"               "ALICE"               "ALICIA"             
  [25] "ALLEN"               "ALLISON"             "ALLISON"            
  [28] "ALLISON"             "ALMA"                "ALMA"               
  [31] "ALMA"                "ALMA"                "ALMA"               
  [34] "ALPHA"               "ALPHA"               "AMELIA"             
  [37] "AMY"                 "ANA"                 "ANA"                
  [40] "ANA"                 "ANA"                 "ANA"                
  [43] "ANA"                 "ANA"                 "ANDREA"             
  [46] "ANDREA"              "ANDREW"              "ANDREW"             
  [49] "ANITA"               "ANNA"                "ANNA"               
  [52] "ANNA"                "ANNA"                "ANNA"               
  [55] "ARLENE"              "ARLENE"              "ARLENE"             
  [58] "ARLENE"              "ARLENE"              "ARLENE"             
  [61] "ARLENE"              "ARLENE"              "ARLENE"             
  [64] "ARLENE"              "ARLENE"              "ARTHUR"             
  [67] "ARTHUR"              "ARTHUR"              "ARTHUR"             
  [70] "ARTHUR"              "ARTHUR"              "ATLANTIC STORM 1"   
  [73] "ATLANTIC STORM 10"   "ATLANTIC STORM 100"  "ATLANTIC STORM 1006"
  [76] "ATLANTIC STORM 1007" "ATLANTIC STORM 1008" "ATLANTIC STORM 1009"
  [79] "ATLANTIC STORM 101"  "ATLANTIC STORM 1010" "ATLANTIC STORM 1011"
  [82] "ATLANTIC STORM 1012" "ATLANTIC STORM 1013" "ATLANTIC STORM 1014"
  [85] "ATLANTIC STORM 1015" "ATLANTIC STORM 102"  "ATLANTIC STORM 1020"
  [88] "ATLANTIC STORM 1021" "ATLANTIC STORM 1022" "ATLANTIC STORM 1025"
  [91] "ATLANTIC STORM 1027" "ATLANTIC STORM 1028" "ATLANTIC STORM 1029"
  [94] "ATLANTIC STORM 103"  "ATLANTIC STORM 1031" "ATLANTIC STORM 1035"
  [97] "ATLANTIC STORM 1037" "ATLANTIC STORM 1038" "ATLANTIC STORM 104" 
 [100] "ATLANTIC STORM 1040" "ATLANTIC STORM 1041" "ATLANTIC STORM 1042"
 [103] "ATLANTIC STORM 1044" "ATLANTIC STORM 1046" "ATLANTIC STORM 1047"
 [106] "ATLANTIC STORM 1048" "ATLANTIC STORM 1049" "ATLANTIC STORM 105" 
 [109] "ATLANTIC STORM 1050" "ATLANTIC STORM 1051" "ATLANTIC STORM 1056"
 [112] "ATLANTIC STORM 1057" "ATLANTIC STORM 106"  "ATLANTIC STORM 1060"
 [115] "ATLANTIC STORM 1061" "ATLANTIC STORM 1064" "ATLANTIC STORM 1065"
 [118] "ATLANTIC STORM 1067" "ATLANTIC STORM 1068" "ATLANTIC STORM 1069"
 [121] "ATLANTIC STORM 107"  "ATLANTIC STORM 1073" "ATLANTIC STORM 1074"
 [124] "ATLANTIC STORM 1078" "ATLANTIC STORM 108"  "ATLANTIC STORM 1080"
 [127] "ATLANTIC STORM 1081" "ATLANTIC STORM 1082" "ATLANTIC STORM 1083"
 [130] "ATLANTIC STORM 1085" "ATLANTIC STORM 1086" "ATLANTIC STORM 1089"
 [133] "ATLANTIC STORM 109"  "ATLANTIC STORM 1090" "ATLANTIC STORM 1092"
 [136] "ATLANTIC STORM 1093" "ATLANTIC STORM 1094" "ATLANTIC STORM 1096"
 [139] "ATLANTIC STORM 1097" "ATLANTIC STORM 1098" "ATLANTIC STORM 1099"
 [142] "ATLANTIC STORM 11"   "ATLANTIC STORM 110"  "ATLANTIC STORM 1101"
 [145] "ATLANTIC STORM 1104" "ATLANTIC STORM 1106" "ATLANTIC STORM 1109"
 [148] "ATLANTIC STORM 111"  "ATLANTIC STORM 1110" "ATLANTIC STORM 1114"
 [151] "ATLANTIC STORM 1119" "ATLANTIC STORM 112"  "ATLANTIC STORM 1120"
 [154] "ATLANTIC STORM 1121" "ATLANTIC STORM 1122" "ATLANTIC STORM 1123"
 [157] "ATLANTIC STORM 1124" "ATLANTIC STORM 1125" "ATLANTIC STORM 1128"
 [160] "ATLANTIC STORM 113"  "ATLANTIC STORM 1131" "ATLANTIC STORM 1132"
 [163] "ATLANTIC STORM 1133" "ATLANTIC STORM 1134" "ATLANTIC 

In [45]:
# output count and order of atlantic hurricanes by top speed
speed_order <- get_storm_names_max_speed(atlantic_data)
length(speed_order)
speed_order

[1] 1873

[1] "ALLEN"               "ATLANTIC STORM 654"  "GILBERT"            
   [4] "WILMA"               "MITCH"               "RITA"               
   [7] "IRMA"                "ATLANTIC STORM 617"  "JANET"              
  [10] "CAMILLE"             "ANITA"               "DAVID"              
  [13] "ANDREW"              "KATRINA"             "DEAN"               
  [16] "FELIX"               "MARIA"               "ATLANTIC STORM 552" 
  [19] "HATTIE"              "ISABEL"              "IVAN"               
  [22] "MATTHEW"             "ATLANTIC STORM 580"  "ATLANTIC STORM 607" 
  [25] "ATLANTIC STORM 626"  "ATLANTIC STORM 632"  "ATLANTIC STORM 693" 
  [28] "CAROL"               "ESTHER"              "BEULAH"             
  [31] "EDITH"               "HUGO"                "EMILY"              
  [34] "MICHAEL"             "ATLANTIC STORM 584"  "ATLANTIC STORM 589" 
  [37] "GEORGES"             "FLOYD"               "LENNY"              
  [40] "GUSTAV"              "IGOR"                "JOAQUIN"            
  [43] "JOSE"                "ATLANTIC STORM 14"   "ATLANTIC STORM 30"  
  [46] "ATLANTIC STORM 202"  "ATLANTIC STORM 245"  "ATLANTIC STORM 364" 
  [49] "ATLANTIC STORM 460"  "ATLANTIC STORM 505"  "ATLANTIC STORM 514" 
  [52] "ATLANTIC STORM 564"  "ATLANTIC STORM 567"  "ATLANTIC STORM 605" 
  [55] "EASY"                "HELENE"              "FLORA"              
  [58] "CLEO"                "INEZ"                "CARMEN"             
  [61] "OPAL"                "GERT"                "CHARLEY"            
  [64] "DENNIS"              "FLORENCE"            "ATLANTIC STORM 372" 
  [67] "ATLANTIC STORM 482"  "ATLANTIC STORM 486"  "ATLANTIC STORM 612" 
  [70] "ATLANTIC STORM 745"  "ATLANTIC STORM 751"  "ATLANTIC STORM 774" 
  [73] "DOG"                 "FOX"                 "DONNA"              
  [76] "CARLA"               "GLORIA"              "HELENE"             
  [79] "JOAN"                "GABRIELLE"           "EDOUARD"            
  [82] "BRET"                "IRIS"                "LILI"               
  [85] "FABIAN"              "FRANCES"             "KARL"               
  [88] "IKE"                 "PALOMA"              "EARL"               
  [91] "GONZALO"             "ATLANTIC STORM 101"  "ATLANTIC STORM 187" 
  [94] "ATLANTIC STORM 208"  "ATLANTIC STORM 224"  "ATLANTIC STORM 527" 
  [97] "ATLANTIC STORM 558"  "ATLANTIC STORM 624"  "ATLANTIC STORM 629" 
 [100] "ATLANTIC STORM 630"  "ATLANTIC STORM 656"  "ATLANTIC STORM 701" 
 [103] "ATLANTIC STORM 731"  "FOX"                 "CONNIE"             
 [106] "IONE"                "CARRIE"              "CLEO"               
 [109] "HILDA"               "BETSY"               "GLADYS"             
 [112] "ELLA"                "FELIX"               "LUIS"               
 [115] "HORTENSE"            "CINDY"               "ISAAC"              
 [118] "KEITH"               "MICHELLE"            "JULIA"              
 [121] "KATIA"               "OPHELIA"             "NICOLE"             
 [124] "ATLANTIC STORM 322"  "ATLANTIC STORM 330"  "ATLANTIC STORM 357" 
 [127] "ATLANTIC STORM 421"  "ATLANTIC STORM 492"  "ATLANTIC STORM 561" 
 [130] "ATLANTIC STORM 596"  "ATLANTIC STORM 653"  "ATLANTIC STORM 715" 
 [133] "ATLANTIC STORM 761"  "ATLANTIC STORM 786"  "ATLANTIC STORM 788" 
 [136] "ATLANTIC STORM 792"  "KING"                "CHARLIE"            
 [139] "HAZEL"               "DAISY"               "GRACIE"             
 [142] "BETSY"               "FRANCES"             "DORA"               
 [145] "GLADYS"              "GRETA"               "FREDERIC"           
 [148] "HARVEY"              "DEBBY"               "DIANA"              
 [151] "CLAUDETTE"           "OMAR"                "BILL"               
 [154] "DANIELLE"            "HARVEY"              "ATLANTIC STORM 22"  
 [157] "ATLANTIC STORM 29"   "ATLANTIC STORM 51"   "ATLANTIC STORM 54"  
 [160] "ATLANTIC STORM 111"  "ATLANTIC STORM 129"  "ATLANTIC STORM 196" 
 [163] "ATLANTIC STORM 220"  "ATLANTIC STORM 226"  "ATLANTIC 

In [46]:
# output count and order of atlantic hurricanes by min pressure
pressure_order <- get_storm_names_min_pressure(atlantic_data)
length(pressure_order)
pressure_order

[1] 1873

[1] "ATLANTIC STORM 1"    "ATLANTIC STORM 2"    "ATLANTIC STORM 3"   
   [4] "ATLANTIC STORM 4"    "ATLANTIC STORM 5"    "ATLANTIC STORM 6"   
   [7] "ATLANTIC STORM 7"    "ATLANTIC STORM 8"    "ATLANTIC STORM 9"   
  [10] "ATLANTIC STORM 10"   "ATLANTIC STORM 11"   "ATLANTIC STORM 12"  
  [13] "ATLANTIC STORM 13"   "ATLANTIC STORM 14"   "ATLANTIC STORM 15"  
  [16] "ATLANTIC STORM 16"   "ATLANTIC STORM 17"   "ATLANTIC STORM 18"  
  [19] "ATLANTIC STORM 19"   "ATLANTIC STORM 20"   "ATLANTIC STORM 21"  
  [22] "ATLANTIC STORM 22"   "ATLANTIC STORM 23"   "ATLANTIC STORM 24"  
  [25] "ATLANTIC STORM 25"   "ATLANTIC STORM 26"   "ATLANTIC STORM 27"  
  [28] "ATLANTIC STORM 28"   "ATLANTIC STORM 29"   "ATLANTIC STORM 30"  
  [31] "ATLANTIC STORM 31"   "ATLANTIC STORM 32"   "ATLANTIC STORM 33"  
  [34] "ATLANTIC STORM 34"   "ATLANTIC STORM 35"   "ATLANTIC STORM 36"  
  [37] "ATLANTIC STORM 37"   "ATLANTIC STORM 38"   "ATLANTIC STORM 39"  
  [40] "ATLANTIC STORM 40"   "ATLANTIC STORM 41"   "ATLANTIC STORM 42"  
  [43] "ATLANTIC STORM 43"   "ATLANTIC STORM 44"   "ATLANTIC STORM 45"  
  [46] "ATLANTIC STORM 46"   "ATLANTIC STORM 47"   "ATLANTIC STORM 48"  
  [49] "ATLANTIC STORM 49"   "ATLANTIC STORM 50"   "ATLANTIC STORM 51"  
  [52] "ATLANTIC STORM 52"   "ATLANTIC STORM 53"   "ATLANTIC STORM 54"  
  [55] "ATLANTIC STORM 55"   "ATLANTIC STORM 56"   "ATLANTIC STORM 57"  
  [58] "ATLANTIC STORM 58"   "ATLANTIC STORM 59"   "ATLANTIC STORM 60"  
  [61] "ATLANTIC STORM 61"   "ATLANTIC STORM 62"   "ATLANTIC STORM 63"  
  [64] "ATLANTIC STORM 64"   "ATLANTIC STORM 65"   "ATLANTIC STORM 66"  
  [67] "ATLANTIC STORM 67"   "ATLANTIC STORM 68"   "ATLANTIC STORM 69"  
  [70] "ATLANTIC STORM 70"   "ATLANTIC STORM 71"   "ATLANTIC STORM 72"  
  [73] "ATLANTIC STORM 73"   "ATLANTIC STORM 74"   "ATLANTIC STORM 75"  
  [76] "ATLANTIC STORM 76"   "ATLANTIC STORM 77"   "ATLANTIC STORM 78"  
  [79] "ATLANTIC STORM 79"   "ATLANTIC STORM 80"   "ATLANTIC STORM 81"  
  [82] "ATLANTIC STORM 82"   "ATLANTIC STORM 83"   "ATLANTIC STORM 84"  
  [85] "ATLANTIC STORM 85"   "ATLANTIC STORM 86"   "ATLANTIC STORM 87"  
  [88] "ATLANTIC STORM 88"   "ATLANTIC STORM 89"   "ATLANTIC STORM 90"  
  [91] "ATLANTIC STORM 91"   "ATLANTIC STORM 92"   "ATLANTIC STORM 93"  
  [94] "ATLANTIC STORM 94"   "ATLANTIC STORM 95"   "ATLANTIC STORM 96"  
  [97] "ATLANTIC STORM 97"   "ATLANTIC STORM 98"   "ATLANTIC STORM 99"  
 [100] "ATLANTIC STORM 100"  "ATLANTIC STORM 101"  "ATLANTIC STORM 102" 
 [103] "ATLANTIC STORM 103"  "ATLANTIC STORM 104"  "ATLANTIC STORM 105" 
 [106] "ATLANTIC STORM 106"  "ATLANTIC STORM 107"  "ATLANTIC STORM 108" 
 [109] "ATLANTIC STORM 109"  "ATLANTIC STORM 110"  "ATLANTIC STORM 111" 
 [112] "ATLANTIC STORM 112"  "ATLANTIC STORM 113"  "ATLANTIC STORM 114" 
 [115] "ATLANTIC STORM 115"  "ATLANTIC STORM 116"  "ATLANTIC STORM 117" 
 [118] "ATLANTIC STORM 118"  "ATLANTIC STORM 119"  "ATLANTIC STORM 120" 
 [121] "ATLANTIC STORM 121"  "ATLANTIC STORM 122"  "ATLANTIC STORM 123" 
 [124] "ATLANTIC STORM 124"  "ATLANTIC STORM 125"  "ATLANTIC STORM 126" 
 [127] "ATLANTIC STORM 127"  "ATLANTIC STORM 128"  "ATLANTIC STORM 129" 
 [130] "ATLANTIC STORM 130"  "ATLANTIC STORM 131"  "ATLANTIC STORM 132" 
 [133] "ATLANTIC STORM 133"  "ATLANTIC STORM 134"  "ATLANTIC STORM 135" 
 [136] "ATLANTIC STORM 136"  "ATLANTIC STORM 137"  "ATLANTIC STORM 138" 
 [139] "ATLANTIC STORM 139"  "ATLANTIC STORM 140"  "ATLANTIC STORM 141" 
 [142] "ATLANTIC STORM 142"  "ATLANTIC STORM 143"  "ATLANTIC STORM 144" 
 [145] "ATLANTIC STORM 145"  "ATLANTIC STORM 146"  "ATLANTIC STORM 147" 
 [148] "ATLANTIC STORM 148"  "ATLANTIC STORM 149"  "ATLANTIC STORM 150" 
 [151] "ATLANTIC STORM 151"  "ATLANTIC STORM 152"  "ATLANTIC STORM 153" 
 [154] "ATLANTIC STORM 154"  "ATLANTIC STORM 155"  "ATLANTIC STORM 156" 
 [157] "ATLANTIC STORM 157"  "ATLANTIC STORM 158"  "ATLANTIC STORM 159" 
 [160] "ATLANTIC STORM 160"  "ATLANTIC STORM 161"  "ATLANTIC STORM 162" 
 [163] "ATLANTIC STORM 163"  "ATLANTIC STORM 164"  "ATLANTIC 